# Lab42

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from time import time
from sklearn.model_selection import train_test_split as split_test_train

from keras.models import Sequential
from keras.layers import Dense, SimpleRNN, LSTM, GRU
from keras.optimizers import RMSprop
from keras.callbacks import Callback
import tensorflow_datasets as tfds
import tensorflow as tf

tfds.disable_progress_bar()

f:\KTU\Neuroninių tinklų metodai\venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [5]:
def plot_graphs(history, metric):
    plt.plot(history.history[metric])
    plt.plot(history.history['val_'+metric], '')
    plt.xlabel("Epochs")
    plt.ylabel(metric)
    plt.legend([metric, 'val_'+metric])

dataset, info = tfds.load('imdb_reviews', with_info=True, as_supervised=True)
train_dataset, test_dataset = dataset['train'], dataset['test']

for example, label in train_dataset.take(1):
  print('text: ', example.numpy())
  print('label: ', label.numpy())

BUFFER_SIZE = 10000
BATCH_SIZE = 64

train_dataset = train_dataset.shuffle(BUFFER_SIZE).batch(BATCH_SIZE).prefetch(tf.data.AUTOTUNE)
test_dataset = test_dataset.batch(BATCH_SIZE).prefetch(tf.data.AUTOTUNE)

for example, label in train_dataset.take(1):
  print('texts: ', example.numpy()[:3])
  print()
  print('labels: ', label.numpy()[:3])

VOCAB_SIZE = 1000
encoder = tf.keras.layers.TextVectorization(max_tokens=VOCAB_SIZE)
encoder.adapt(train_dataset.map(lambda text, label: text))

model = tf.keras.Sequential([
    encoder,
    tf.keras.layers.Embedding(
        input_dim=len(encoder.get_vocabulary()),
        output_dim=64,
        # Use masking to handle the variable sequence lengths
        mask_zero=True
    ),
    tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(64)),
    tf.keras.layers.Dense(64, activation='relu'),
    tf.keras.layers.Dense(1)
])

model.compile(
    loss=tf.keras.losses.BinaryCrossentropy(from_logits=True),
    optimizer=tf.keras.optimizers.Adam(1e-4),
    metrics=['accuracy']
)

checkpoint = tf.train.Checkpoint(
    model=model
)


text:  b"This was an absolutely terrible movie. Don't be lured in by Christopher Walken or Michael Ironside. Both are great actors, but this must simply be their worst role in history. Even their great acting could not redeem this movie's ridiculous storyline. This movie is an early nineties US propaganda piece. The most pathetic scenes were those when the Columbian rebels were making their cases for revolutions. Maria Conchita Alonso appeared phony, and her pseudo-love affair with Walken was nothing but a pathetic emotional plug in a movie that was devoid of any real meaning. I am disappointed that there are movies like this, ruining actor's like Christopher Walken's good name. I could barely sit through it."
label:  0
texts:  [b'Closer to reality and containing more depth than "Breakdance", Stan Lathan\'s "Beat Street" is still a pretty dull show. Again this pic is really only cashing in on the \'breakin\' craze but at least we get a little bit of entertainment from the plot, which c

In [14]:
history = model.fit(
    train_dataset,
    epochs=10,
    validation_data=test_dataset,
    validation_steps=30
)

Epoch 1/10



391/391 [==============================] - 439s 1s/step - loss: 0.6559 - accuracy: 0.5520 - val_loss: 0.5300 - val_accuracy: 0.7615
Epoch 2/10
391/391 [==============================] - 428s 1s/step - loss: 0.4360 - accuracy: 0.7975 - val_loss: 0.3924 - val_accuracy: 0.8203
Epoch 3/10
391/391 [==============================] - 852s 2s/step - loss: 0.3608 - accuracy: 0.8432 - val_loss: 0.3666 - val_accuracy: 0.8250
Epoch 4/10
391/391 [==============================] - 1106s 3s/step - loss: 0.3334 - accuracy: 0.8585 - val_loss: 0.3467 - val_accuracy: 0.8349
Epoch 5/10
391/391 [==============================] - 716s 2s/step - loss: 0.3153 - accuracy: 0.8655 - val_loss: 0.3263 - val_accuracy: 0.8568
Epoch 6/10
391/391 [==============================] - 1155s 3s/step - loss: 0.3116 - accuracy: 0.8684 - val_loss: 0.3270 - val_accuracy: 0.8542
Epoch 7/10
391/391 [==============================] - 1022s 3s/step - loss: 0.3037 - accuracy: 0.8723 - val_loss: 0.3213 - val_accuracy: 0.8578
Epoch 8

In [5]:
checkpoint.restore(tf.train.latest_checkpoint("."))

In [6]:
test_loss, test_acc = model.evaluate(test_dataset)

print('Test Loss:', test_loss)
print('Test Accuracy:', test_acc)

391/391 [==============================] - 48s 115ms/step - loss: 0.3387 - accuracy: 0.8605
Test Loss: 0.3387344777584076
Test Accuracy: 0.8605200052261353


In [7]:
checkpoint.save(file_prefix = "./reference/RNN_chpt")

FailedPreconditionError: ./reference is not a directory

### 2. Pakeiskite tokius parametrus kaip buferio dydis ir žodyno dydis.

In [2]:
BUFFER_SIZE = 1000
BATCH_SIZE = 64
VOCAB_SIZE = 100

dataset, info = tfds.load('imdb_reviews', with_info=True, as_supervised=True)
train_dataset, test_dataset = dataset['train'], dataset['test']

train_dataset = train_dataset.shuffle(BUFFER_SIZE).batch(BATCH_SIZE).prefetch(tf.data.AUTOTUNE)
test_dataset = test_dataset.batch(BATCH_SIZE).prefetch(tf.data.AUTOTUNE)

encoder = tf.keras.layers.TextVectorization(max_tokens=VOCAB_SIZE)
encoder.adapt(train_dataset.map(lambda text, label: text))

model = tf.keras.Sequential([
    encoder,
    tf.keras.layers.Embedding(
        input_dim=len(encoder.get_vocabulary()),
        output_dim=64,
        # Use masking to handle the variable sequence lengths
        mask_zero=True
    ),
    tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(64)),
    tf.keras.layers.Dense(64, activation='relu'),
    tf.keras.layers.Dense(1)
])

model.compile(
    loss=tf.keras.losses.BinaryCrossentropy(from_logits=True),
    optimizer=tf.keras.optimizers.Adam(1e-4),
    metrics=['accuracy']
)

checkpoint = tf.train.Checkpoint(
    model=model
)


In [3]:
history = model.fit(
    train_dataset,
    epochs=10,
    validation_data=test_dataset,
    validation_steps=30
)

Epoch 1/10



391/391 [==============================] - 419s 1s/step - loss: 0.6884 - accuracy: 0.5036 - val_loss: 0.6677 - val_accuracy: 0.4917
Epoch 2/10
391/391 [==============================] - 483s 1s/step - loss: 0.6242 - accuracy: 0.5987 - val_loss: 0.6088 - val_accuracy: 0.6245
Epoch 3/10
391/391 [==============================] - 451s 1s/step - loss: 0.5704 - accuracy: 0.6875 - val_loss: 0.5618 - val_accuracy: 0.7161
Epoch 4/10
391/391 [==============================] - 461s 1s/step - loss: 0.5462 - accuracy: 0.7132 - val_loss: 0.5517 - val_accuracy: 0.7167
Epoch 5/10
391/391 [==============================] - 473s 1s/step - loss: 0.5398 - accuracy: 0.7162 - val_loss: 0.5479 - val_accuracy: 0.7078
Epoch 6/10
391/391 [==============================] - 471s 1s/step - loss: 0.5335 - accuracy: 0.7213 - val_loss: 0.5417 - val_accuracy: 0.7115
Epoch 7/10
391/391 [==============================] - 495s 1s/step - loss: 0.5311 - accuracy: 0.7222 - val_loss: 0.5438 - val_accuracy: 0.7120
Epoch 8/10

In [8]:
test_loss, test_acc = model.evaluate(test_dataset)

print('Test Loss:', test_loss)
print('Test Accuracy:', test_acc)

plot_graphs(history, 'accuracy')

RuntimeError: You must compile your model before training/testing. Use `model.compile(optimizer, loss)`.

### 3. Pakeiskite Bidirectional sluoksnį į paprastą RNN ir palyginkite modelių tikslumą.

In [7]:
model = tf.keras.Sequential([
    encoder,
    tf.keras.layers.Embedding(
        input_dim=len(encoder.get_vocabulary()),
        output_dim=64,
        # Use masking to handle the variable sequence lengths
        mask_zero=True
    ),
    tf.keras.layers.SimpleRNN(64),
    tf.keras.layers.Dense(64, activation='relu'),
    tf.keras.layers.Dense(1)
])